![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 6,7. <i>Preprocessing i postprocessing</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Na dzisiejszych zajęciach zajmiemy się niezwykle przydatnymi narzędziami wspomagającymi pracę tłumacza. W odróżnieniu od dotychczas poznanych, nie są one oparte na pamięci tłumaczeń, ani na słownikach. Chodzi o techniki preprocessingu i postprocessingu.

Proces tłumaczenia przeprowadzony w pełni profesjonalnie składa się z wielu faz, które angażują nie tylko tłumaczy, ale także kierowników projektu, analityków, czy korektorów. Każda z tych osób do swojej pracy może wykorzystywać system informatyczny, do którego na początku całego procesu trafiają pliki do tłumaczenia. Oznacza to, że zanim tekst źródłowy trafi do tłumacza, system ma jeszcze szansę coś w nim zmienić. A kiedy tłumacz wykona już swoją pracę, można uruchomić kolejny mechanizm, który zmodyfikuje tłumaczenie przed oddaniem go do zamawiającego. Jak się domyślamy, modyfikacje tekstu przed przekazaniem go do tłumacza nazywamy **preprocessingiem**, natomiast te dokonywane po wykonaniu tłumaczenia (ale przed zwróceniem go do klienta) nazywamy **postprocessingiem**. Terminy te, będące mało zgrabnymi kalkami z języka angielskiego, mają wersje prawdziwie polskie: przetwarzanie wstępne i końcowe. Wersje te są jednak stosowane na tyle rzadko, że mogą jedynie wprowadzić zamieszanie (co w gruncie rzeczy jest dość smutne).

Typowe operacje w fazie preprocessingu obejmują:
* identyfikację tagów xmlowych (które często są później wyświetlane w interfejsie CAT-a jako jeden niepodzielny znak)
* identyfikację segmentów, których nie należy tłumaczyć (na przykład składających się z samych liczb)

* identyfikację dat i jednostek miary w tekście źródłowym

We wszystkich tych operacjach niezwykle przydatne okazują się wyrażenia regularne.

### Ćwiczenie 1: Używając wyrażeń regularnych napisz funkcję do znajdowania wszystkich tagów XML w tekście. Funkcja powinna zwracać pozycje, na których znalazła tagi.

In [1]:
import re

def find_tags(string):
    pattern = r'<[^>]+>'
    matches = re.finditer(pattern, string)
    tag_indexes = [(match.start(), match.end()) for match in matches]
    return tag_indexes

In [5]:
string = "<tag1>ADIOS</tag1><tag2>OLA</tag2>"
[ string[out[0]:out[1]] for out in find_tags(string)]

['<tag1>', '</tag1>', '<tag2>', '</tag2>']

### Ćwiczenie 2: Używając wyrażeń regularnych napisz funkcję do identyfikacji segmentów, których nie należy tłumaczyć. Zastosuj wymyślone przez siebie kryteria. Funkcja is_translatable powinna zwracać True, jeśli segment powinien być przetłumaczony przez tłumacza (zwykłe zdanie). False powinno być zwrócone, kiedy segment jest nieprzetłumaczalny i powinien zostać skopiowany (np. 4.2.1.)

In [20]:
import re
import string

def is_translatable(text):
    return bool(re.match(r'^[^0-9IVXLCDM\s' + re.escape(string.punctuation) + ']+$', text))

text1 = "This is a sample text."
text2 = "2024."
text3 = "Это пример текста."
text4 = "おはよう"

print(is_translatable(text1)) 
print(is_translatable(text2))
print(is_translatable(text3))
print(is_translatable(text4))

False
False
False
True


In [32]:
import re
import string

def is_translatable(text):
    return bool(re.match(r'^[^\d]+$|^\s+$', text))

examples = ["This is a sample text.", "2024.", 
            "Это пример текста.", "おはよう"]

for ex in examples:
    response = 'Yes' if is_translatable(ex) else 'No'
    print(f'"{ex}" is translatable?\n{response}')

"This is a sample text." is translatable?
Yes
"2024." is translatable?
No
"Это пример текста." is translatable?
Yes
"おはよう" is translatable?
Yes


### Ćwiczenie 3: Używając wyrażeń regularnych napisz funkcję do identyfikacji i interpretacji 5 wybranych przez siebie formatów daty. Funkcja powinna zwracać pozycje, na których odnalazła daty oraz dzień, miesiąc i rok, które ta data reprezentuje.

In [44]:
import re

def find_dates(text):
    date_formats = [
        (r'(\d{1,2})[-/](\d{1,2})[-/](\d{2,4})', 'day_first'),
        (r'(\d{1,2})[/](\d{1,2})[/](\d{2,4})', 'month_first'),
        (r'(\d{1,2}) (\w{3,9}) (\d{4})', 'day_first'),
        (r'(\d{1,2})-(\d{1,2})-(\d{2,4})', 'day_first'),
        (r'(\d{1,2}) (\w{3,9}),? (\d{4})', 'day_first')
    ]

    months = {
        'January': 1, 'February': 2, 'March': 3, 'April': 4, 'May': 5, 'June': 6,
        'July': 7, 'August': 8, 'September': 9, 'October': 10, 'November': 11, 'December': 12
    }

    dates_found = []
    for date_pattern, format_type in date_formats:
        matches = re.finditer(date_pattern, text)
        for match in matches:
            groups = match.groups()
            if len(groups) == 3:
                if format_type == 'day_first':
                    day, month, year = groups
                else:
                    month, day, year = groups
                if month.isdigit():
                    month = int(month)
                else:
                    month = months[month]
                dates_found.append((match.group(), int(day), month, int(year)))
            elif len(groups) == 4:
                if format_type == 'day_first':
                    day, month, _, year = groups
                else:
                    month, day, _, year = groups
                if month.isdigit():
                    month = int(month)
                else:
                    month = months[month]
                dates_found.append((match.group(), int(day), month, int(year)))
    return dates_found

text = "Here are some dates: 03/25/2022, 25-12-2023, 12 March 2024, 09/30/2025, 15 September, 2026"
dates = find_dates(text)
for date in dates:
    print(f"{date}\tday:\t{date[1]}\tmonth:\t{date[2]}\tyear:\t{date[3]}")

('03/25/2022', 3, 25, 2022)	day:	3	month:	25	year:	2022
('25-12-2023', 25, 12, 2023)	day:	25	month:	12	year:	2023
('09/30/2025', 9, 30, 2025)	day:	9	month:	30	year:	2025
('03/25/2022', 25, 3, 2022)	day:	25	month:	3	year:	2022
('09/30/2025', 30, 9, 2025)	day:	30	month:	9	year:	2025
('12 March 2024', 12, 3, 2024)	day:	12	month:	3	year:	2024
('25-12-2023', 25, 12, 2023)	day:	25	month:	12	year:	2023
('12 March 2024', 12, 3, 2024)	day:	12	month:	3	year:	2024
('15 September, 2026', 15, 9, 2026)	day:	15	month:	9	year:	2026


Po preprocessingu i tłumaczeniu czas na postprocessing. Ponieważ wykonywany jest on na przetłumaczonym tekście, jego głównym zadaniem jest eliminacja błędów popełnionych przez tłumacza w fazie tłumaczenia. Podczas postprocessingu najczęściej wykonuje się:
* korektę pisowni dla języka docelowego
* usuwanie błędów typograficznych z tekstu (np. wielokrotne spacje, brak spacji po przecinku)
Stanowi to bardzo ważne wsparcie dla edytorów i korektorów, czyli osób sprawdzających pracę tłumacza.

Jednak nowoczesne CAT-y potrafią coś jeszcze. Są w stanie w sprytny sposób wykorzystać kombinację pre- i postprocessingu do wyręczenia tłumacza w żmudnych i technicznych czynnościach. Wykonajmy następujące ćwiczenie:

### Ćwiczenie 4: Wykorzystując funkcję find_dates napisz funkcję do obsługi dat w tłumaczeniu. Wejściem jest segment źródłowy oraz docelowy, które zawierają daty, przy czym daty te mogą być w różnych formatach. Dodatkowym parametrem wejściowym jest nazwa oczekiwanego formatu daty w tłumaczeniu (np. "Europe", "US", "digit-dot". Funkcja najpierw sprawdza, czy liczba dat w tłumaczeniu zgadza się z liczbą dat w segmencie źródłowym oraz czy odpowiadające sobie daty wskazują na ten sam dzień. Jeśli nie, wypisywane jest stosowne ostrzeżenie. Oczekiwanym wyjściem jest segment docelowy, w którym wszystkie daty są w żądanym formacie. 

In [4]:
def correct_dates(source_segment, target_segment, date_format):
    return ''

Co jeszcze można zrobić? Zajmijmy się tagami XML. Z punktu widzenia tłumacza najlepiej byłoby, gdyby mógł przetłumaczyć segment źródłowy zawierający tagi XML na język docelowy zupełnie ignorując te tagi. Ponieważ jednak tagi muszą jakoś znaleźć się w segmencie docelowym, przydałaby się jakaś "magiczna różdżka", która przeniosłaby wszystkie tagi ze źródła do tłumaczenia na mniej więcej dobre miejsca. Spełnijmy marzenie tłumacza!

Rozważmy następujący algorytm: na wejściu mamy segment źródłowy zawierający tagi oraz segment docelowy bez tagów. Dokonujemy tokenizacji segmentu źródłowego tak, aby tagi były osobnymi tokenami. Następnie przeprowadźmy tokenizację segmentu docelowego. Gdy to jest gotowe, możemy zabrać się za przenoszenie (kopiowanie) tagów z segmentu źródłowego do docelowego.

![Transfer tagów](img/tagtransfer.png)

Gdzie w segmencie docelowym powinien trafić tag? Przede wszystkim pomiędzy tokeny - nie chcemy rozbijać słów tagami. Pytanie tylko, pomiędzy które tokeny? Jeśli sytuacja jest taka, jak powyżej, kiedy segment źródłowy i docelowy mają taką samą liczbę słów nie będących tagami, przenosimy tagi na odpowiadające pozycje w tłumaczeniu. Natomiast jeśli długość tłumaczenia jest inna niż źródła, należy obliczać te pozycje w sposób proporcjonalny - jeśli np. mamy tag w źródle na pozycji 3, a tłumaczenie jest dwa razy dłuższe niż źródło, tag powinien być przeniesiony do tłumaczenia na pozycję 6. W przypadku niecałkowitych wartości proporcji stosujemy zaokrąglenia.

### Ćwiczenie 5: Zaimplementuj opisany algorytm transferu tagów.

In [5]:
def transfer_tags(source_segment, target_segment):
    return ''